In [1]:
import numpy as np
import pandas as pd
import math
import re
from collections import Counter
from functools import cmp_to_key
from itertools import product, permutations, combinations, combinations_with_replacement
from itertools import repeat

In [2]:
with open("12-input", "r") as file:
    lines = file.readlines()
data_raw = [line.replace("\n", "") for line in lines]
data_raw = "\n".join(data_raw)
data_raw

'..?????#??.?##? 1,1,2,3\n###?.#???.?#.# 4,2,2,1\n?????##???#? 7,1\n??????#.?#####?? 1,1,1,6\n????#?#.??#?# 3,3,3\n?????#?#.? 2,2,1\n..???.??#??? 3,3,1\n????.??????##??#?#? 2,2,9\n??.#??##??.#?? 2,5,1,1\n.???????????#? 5,1,1\n???.????#??? 2,6,1\n?#???.??#?##??#?.# 2,8,1\n?????.???? 2,2\n????#?#??.?#?.? 1,1,5,1,1\n..?#??#???#?????. 5,6\n??.#..??#??????#???? 2,1,10\n????.????#.??.#??? 1,1,5,1,1,1\n?????????#?##?.. 1,6\n.??.??.??#????? 1,4\n?????.??#????#? 1,8\n?.???????##????#?.?? 14,2\n?#.????#.????.? 1,2,1,1,1\n?#??.???????? 1,1,7\n.????.??????.# 3,3,1,1\n???#??#?.?...? 5,1,1\n.???#???.##??? 2,2\n???#???..?#?? 6,1\n#??.???.#? 3,1,1\n??#???.###???#?.?? 4,3,2,1\n?.?.?????????. 1,1,1,2\n.?.??..???????? 2,5\n?#?#???????.?.?.? 5,4,1,1,1\n??#?#????##??.???? 5,6,2\n???.#?###????.? 1,6,1,1\n.???.??.#?#??? 2,4\n##?#?????#?.#?# 5,2,3\n.##????#?#??#?#??. 3,9,1\n???????#???.??#??? 7,4\n?????..?#??#?#??###? 1,1,1,5,1,5\n.????.??????.##???. 3,2,1,5\n????.#????#?.# 3,7,1\n.???????.?# 5,1\n.???.?#??.?

In [3]:
test_data_raw = """#.#.### 1,1,3
.#...#....###. 1,1,3
.#.###.#.###### 1,3,1,6
####.#...#... 4,1,1
#....######..#####. 1,6,5
.###.##....# 3,2,1"""

test_data_raw2 = """???.### 1,1,3
.??..??...?##. 1,1,3
?#?#?#?#?#?#?#? 1,3,1,6
????.#...#... 4,1,1
????.######..#####. 1,6,5
?###???????? 3,2,1"""

def preprocess_data (data):
    rows = [(row.split(" ")[0], [int(num) for num in row.split(" ")[1].split(",")]) for row in data.split("\n")]
    return rows

test_data_1 = preprocess_data(test_data_raw)
test_data_2 = preprocess_data(test_data_raw2)
test_data_2

[('???.###', [1, 1, 3]),
 ('.??..??...?##.', [1, 1, 3]),
 ('?#?#?#?#?#?#?#?', [1, 3, 1, 6]),
 ('????.#...#...', [4, 1, 1]),
 ('????.######..#####.', [1, 6, 5]),
 ('?###????????', [3, 2, 1])]

In [4]:
data = preprocess_data(data_raw)
data

[('..?????#??.?##?', [1, 1, 2, 3]),
 ('###?.#???.?#.#', [4, 2, 2, 1]),
 ('?????##???#?', [7, 1]),
 ('??????#.?#####??', [1, 1, 1, 6]),
 ('????#?#.??#?#', [3, 3, 3]),
 ('?????#?#.?', [2, 2, 1]),
 ('..???.??#???', [3, 3, 1]),
 ('????.??????##??#?#?', [2, 2, 9]),
 ('??.#??##??.#??', [2, 5, 1, 1]),
 ('.???????????#?', [5, 1, 1]),
 ('???.????#???', [2, 6, 1]),
 ('?#???.??#?##??#?.#', [2, 8, 1]),
 ('?????.????', [2, 2]),
 ('????#?#??.?#?.?', [1, 1, 5, 1, 1]),
 ('..?#??#???#?????.', [5, 6]),
 ('??.#..??#??????#????', [2, 1, 10]),
 ('????.????#.??.#???', [1, 1, 5, 1, 1, 1]),
 ('?????????#?##?..', [1, 6]),
 ('.??.??.??#?????', [1, 4]),
 ('?????.??#????#?', [1, 8]),
 ('?.???????##????#?.??', [14, 2]),
 ('?#.????#.????.?', [1, 2, 1, 1, 1]),
 ('?#??.????????', [1, 1, 7]),
 ('.????.??????.#', [3, 3, 1, 1]),
 ('???#??#?.?...?', [5, 1, 1]),
 ('.???#???.##???', [2, 2]),
 ('???#???..?#??', [6, 1]),
 ('#??.???.#?', [3, 1, 1]),
 ('??#???.###???#?.??', [4, 3, 2, 1]),
 ('?.?.?????????.', [1, 1, 1, 2]),
 ('

In [7]:

def check_damage_validity(springs, damage_sizes):
    groups = [group for group in springs.split(".") if group]
    if len(groups) != len(damage_sizes):
        return False    
    else:
        for group, size in zip(groups, damage_sizes):
            if len(group) != size:
                return False
        return True

for springs, damage_sizes in test_data_1:
    assert check_damage_validity(springs, damage_sizes)

assert check_damage_validity(".#.###.#...######." , [1,3,1,6])
assert not check_damage_validity(".#.###.#...######." , [1,3,1]) 
assert not check_damage_validity(".#.###.##...#####." , [1,3,1,6]) 

def solution (data, verbose=False):
    num_arrangements = []

    for spring_group, damage_sizes in data:
        count_unknown = spring_group.count("?")
        damage_count = spring_group.count("#")
        missing_damage = sum(damage_sizes) - damage_count

        if verbose:
            print("\n", spring_group, damage_sizes)
            print("Count unknown", count_unknown)
            print("Known damages", damage_count)
            print("Missing damage", missing_damage)

        num_arragment = 0
        for combination in list(product(".#", repeat=count_unknown)):
            filled_group = spring_group
            if "".join(combination).count("#") == missing_damage:
                for repl in combination:
                    filled_group = filled_group.replace("?", repl, 1)
                if verbose:
                    print("Checking comb",  combination)
                    print("Resulting string", filled_group)
                if check_damage_validity(filled_group, damage_sizes):
                    num_arragment += 1
                    if verbose:
                        print("Success")
                else:
                    if verbose:
                        print("Error")

        num_arrangements.append(num_arragment)        

    return num_arrangements


sol_1 = solution(data)
# sol = solution(test_data_2, verbose=True)

print(sol_1)
display(sum(sol_1))



[8, 1, 3, 12, 1, 2, 3, 15, 2, 10, 2, 4, 13, 1, 5, 3, 12, 13, 14, 10, 2, 17, 2, 6, 4, 2, 2, 3, 12, 66, 5, 3, 9, 6, 3, 2, 1, 12, 1, 12, 2, 3, 4, 5, 5, 3, 5, 5, 4, 23, 1, 2, 85, 10, 1, 2, 11, 9, 16, 4, 5, 25, 25, 1, 2, 3, 6, 4, 2, 2, 7, 5, 6, 1, 6, 31, 25, 4, 7, 2, 10, 3, 16, 3, 4, 2, 10, 16, 2, 15, 4, 10, 5, 2, 4, 2, 4, 2, 6, 4, 20, 9, 2, 8, 2, 4, 4, 5, 16, 10, 1, 6, 1, 3, 9, 28, 4, 85, 12, 2, 1, 6, 2, 6, 1, 2, 4, 1, 20, 3, 9, 3, 6, 21, 11, 46, 1, 4, 2, 12, 6, 4, 1, 2, 4, 2, 3, 2, 4, 15, 5, 34, 7, 3, 1, 7, 2, 1, 2, 49, 1, 2, 10, 6, 10, 4, 6, 8, 7, 1, 1, 5, 1, 3, 1, 1, 10, 3, 12, 8, 12, 47, 2, 3, 1, 13, 2, 2, 7, 7, 40, 8, 4, 1, 15, 5, 15, 20, 1, 12, 8, 2, 9, 2, 4, 6, 4, 19, 2, 8, 3, 2, 4, 4, 16, 15, 2, 14, 3, 18, 6, 1, 3, 21, 6, 7, 9, 4, 4, 4, 4, 12, 2, 6, 4, 2, 1, 24, 7, 2, 7, 8, 4, 6, 12, 70, 1, 6, 17, 1, 20, 3, 11, 10, 16, 8, 4, 5, 7, 2, 7, 3, 10, 32, 40, 2, 3, 1, 6, 8, 4, 1, 5, 4, 6, 1, 5, 54, 13, 18, 4, 16, 2, 2, 3, 2, 10, 6, 4, 6, 2, 3, 1, 10, 4, 1, 12, 4, 6, 19, 2, 3, 34, 6, 2, 1, 

7716

In [9]:
# Better part1
# full data -> 7716
# test_data -> 21

def solution (data, verbose=False):
    num_arrangements = []
    
    for spring_group, damage_sizes in data:
        
        def calc_combinations (sgroup, sizes, level):
            if verbose:
                print("    "*level,"-------------")
                print("    "*level, sgroup, sizes)
            if not sizes and (sgroup.count("#") == 0):
                if verbose:
                    print("    "*level,"Correct")
                return 1
            
            if sum(sizes) > (sgroup.count("?") + sgroup.count("#")) or (sgroup.count("#") > sum(sizes)):
                if verbose:
                    print("    "*level,"Error")
                return 0 
            
            size = sizes[0]

            combinations = 0
            start_indices = [i for i, character in enumerate(sgroup) if character in ('?', '#')]
            if verbose:
                print("    "*level, start_indices)
            for start_idx in start_indices:
                if verbose:
                    print("    "*level, "Start Index", start_idx)
                if start_idx == 0 or (start_idx > 0 and sgroup[:start_idx].count("#") == 0):
                    # need enough space to fill size
                    enough_space = len(sgroup[start_idx:]) >= size
                    # need to close with ? or . or if sgroup ended
                    closing_possible = enough_space and ((len(sgroup) == start_idx+size) or (sgroup[start_idx+size] in (".", "?")))
                    # need to have only ? or # in this sequence 
                    all_damaged_or_unknown = sgroup[start_idx:start_idx+size].count(".") == 0
                    if enough_space and all_damaged_or_unknown and closing_possible:
                        sgroup_before = sgroup[:start_idx].replace("?", ".")
                        sgroup_current = sgroup[start_idx:start_idx+size].replace("?", "#")
                        # sgroup_close = sgroup[start_idx+size].replace("?", ".")
                        if len(sgroup) > start_idx+size+1:
                            sgroup_rest = sgroup[start_idx+size+1:]
                        else:
                            sgroup_rest = ""
                        
                        if verbose:
                            print("    "*level, sgroup_before+sgroup_current, "   ", size)
                        
                        if check_damage_validity(sgroup_before+sgroup_current, [size]):
                            sizes_next = sizes[1:] if len(sizes) > 1 else []
                            if verbose:
                                print("    "*level, "Continue with", sgroup_rest, " for ", sizes_next)
                            combinations += 1*calc_combinations(sgroup_rest, sizes[1:], level+1)
            return combinations

        num_arrangements.append(calc_combinations(spring_group, damage_sizes, 0))


    return num_arrangements


sol = solution(data)
# sol_test = solution(test_data_2, verbose=False)
print(sol_1)
print(sol)

for idx, (a,b) in enumerate(zip(sol, sol_1)):
    if a != b:
        print(data[idx], "index", idx)
        print("real solution", b)
        print("wrong solution", a)

print(sum(sol))
assert sum(sol) == 7716
# assert sum(sol_test) == 21

[8, 1, 3, 12, 1, 2, 3, 15, 2, 10, 2, 4, 13, 1, 5, 3, 12, 13, 14, 10, 2, 17, 2, 6, 4, 2, 2, 3, 12, 66, 5, 3, 9, 6, 3, 2, 1, 12, 1, 12, 2, 3, 4, 5, 5, 3, 5, 5, 4, 23, 1, 2, 85, 10, 1, 2, 11, 9, 16, 4, 5, 25, 25, 1, 2, 3, 6, 4, 2, 2, 7, 5, 6, 1, 6, 31, 25, 4, 7, 2, 10, 3, 16, 3, 4, 2, 10, 16, 2, 15, 4, 10, 5, 2, 4, 2, 4, 2, 6, 4, 20, 9, 2, 8, 2, 4, 4, 5, 16, 10, 1, 6, 1, 3, 9, 28, 4, 85, 12, 2, 1, 6, 2, 6, 1, 2, 4, 1, 20, 3, 9, 3, 6, 21, 11, 46, 1, 4, 2, 12, 6, 4, 1, 2, 4, 2, 3, 2, 4, 15, 5, 34, 7, 3, 1, 7, 2, 1, 2, 49, 1, 2, 10, 6, 10, 4, 6, 8, 7, 1, 1, 5, 1, 3, 1, 1, 10, 3, 12, 8, 12, 47, 2, 3, 1, 13, 2, 2, 7, 7, 40, 8, 4, 1, 15, 5, 15, 20, 1, 12, 8, 2, 9, 2, 4, 6, 4, 19, 2, 8, 3, 2, 4, 4, 16, 15, 2, 14, 3, 18, 6, 1, 3, 21, 6, 7, 9, 4, 4, 4, 4, 12, 2, 6, 4, 2, 1, 24, 7, 2, 7, 8, 4, 6, 12, 70, 1, 6, 17, 1, 20, 3, 11, 10, 16, 8, 4, 5, 7, 2, 7, 3, 10, 32, 40, 2, 3, 1, 6, 8, 4, 1, 5, 4, 6, 1, 5, 54, 13, 18, 4, 16, 2, 2, 3, 2, 10, 6, 4, 6, 2, 3, 1, 10, 4, 1, 12, 4, 6, 19, 2, 3, 34, 6, 2, 1, 

In [10]:
sol = solution([data[2]], verbose=True)

 -------------
 ?????##???#? [7, 1]
 [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]
 Start Index 0
 #######     7
 Continue with ??#?  for  [1]
     -------------
     ??#? [1]
     [0, 1, 2, 3]
     Start Index 0
     #     1
     Continue with #?  for  []
         -------------
         #? []
         Error
     Start Index 1
     Start Index 2
     ..#     1
     Continue with   for  []
         -------------
          []
         Correct
     Start Index 3
 Start Index 1
 .#######     7
 Continue with ?#?  for  [1]
     -------------
     ?#? [1]
     [0, 1, 2]
     Start Index 0
     Start Index 1
     .#     1
     Continue with   for  []
         -------------
          []
         Correct
     Start Index 2
 Start Index 2
 ..#######     7
 Continue with #?  for  [1]
     -------------
     #? [1]
     [0, 1]
     Start Index 0
     #     1
     Continue with   for  []
         -------------
          []
         Correct
     Start Index 1
 Start Index 3
 Start Index 4
 ....#######     

# Part 2

In [11]:

def check_damage_validity(springs, damage_sizes):
    groups = [group for group in springs.split(".") if group]
    if len(groups) != len(damage_sizes):
        return False    
    else:
        for group, size in zip(groups, damage_sizes):
            if len(group) != size:
                return False
        return True

for springs, damage_sizes in test_data_1:
    assert check_damage_validity(springs, damage_sizes)

assert check_damage_validity(".#.###.#...######." , [1,3,1,6])
assert not check_damage_validity(".#.###.#...######." , [1,3,1]) 
assert not check_damage_validity(".#.###.##...#####." , [1,3,1,6]) 


In [33]:
def encode(sgroup, sizes):
    return sgroup + ",".join([str(i) for i in sizes])

def solution (data, verbose=False):
    num_arrangements = []
    frame = pd.DataFrame()
    cache = {}

    for idx, (spring_group, damage_sizes) in enumerate(data):
        print(f"{str(idx+1)}/{str(len(data))}")

        

        def calc_combinations (sgroup, sizes, level, cache={}):
            if verbose:
                print("    "*level,"-------------")
                print("    "*level, sgroup, sizes)

            if not sizes and (sgroup.count("#") == 0):
                if verbose:
                    print("    "*level,"Correct")
                return 1
            
            if (sum(sizes) > (sgroup.count("?") + sgroup.count("#"))):
                if verbose:
                    print("    "*level,f"Error, need {int(sum(sizes))} but only have {int((sgroup.count('?') + sgroup.count('#')))} ? and # to allocate ")
                return 0 
            
            if sum(sizes) < sgroup.count("#"):
                if verbose:
                    print("    "*level,f"Error, {sgroup.count('#')} of # cannot be allocated by {int(sum(sizes))} of sizes")
                return 0 

            size = sizes[0]

            combinations = 0
            start_indices = [i for i, character in enumerate(sgroup) if character in ('?', '#')]
            if verbose:
                print("    "*level, start_indices)
            for start_idx in start_indices:
                if verbose:
                    print("    "*level, "Start Index", start_idx)
                if sgroup[:start_idx].count("#") == 0:
                    # need enough space to fill size
                    enough_space = len(sgroup[start_idx:]) >= size
                    # need to close with ? or . or if sgroup ended
                    closing_possible = enough_space and ((len(sgroup) == start_idx+size) or (sgroup[start_idx+size] in (".", "?")))
                    # need to have only ? or # in this sequence 
                    all_damaged_or_unknown = sgroup[start_idx:start_idx+size].count(".") == 0
                    if (len(sgroup) > start_idx+size+1) and (len(sizes) > 1):
                        extension_possible = (sgroup[start_idx+size+1:].count("?") + sgroup[start_idx+size+1:].count("#")) >= sum(sizes[1:])
                    else:
                        extension_possible = True
                    before_healthy = sgroup[:start_idx].count("#") == 0
                    
                    if enough_space and all_damaged_or_unknown and closing_possible and extension_possible and before_healthy:
                        sgroup_before = sgroup[:start_idx].replace("?", ".")
                        sgroup_current = sgroup[start_idx:start_idx+size].replace("?", "#")
                        # sgroup_close = sgroup[start_idx+size].replace("?", ".")
                        if len(sgroup) > start_idx+size+1:
                            sgroup_rest = sgroup[start_idx+size+1:]
                        else:
                            sgroup_rest = ""
                        
                        if verbose:
                            print("    "*level, sgroup_before+sgroup_current, "   ", size)
                        
                        if check_damage_validity(sgroup_before+sgroup_current, [size]):
                            sizes_next = sizes[1:] if len(sizes) > 1 else []
                            if verbose:
                                print("    "*level, "Continue with", sgroup_rest, " for ", sizes_next)
                            
                            encoded_input = encode(sgroup_rest, sizes_next)
                            if encoded_input in cache:
                                if verbose:
                                    print("    "*level,"Cache hit", encoded_input, cache[encoded_input])
                                combs_next = cache[encoded_input]
                            else:
                                combs_next = calc_combinations(sgroup_rest, sizes_next, level+1, cache)
                                cache[encoded_input] = combs_next
                                if verbose:
                                    print("    "*level,"Saving to cache", encoded_input, combs_next)
                            combinations += 1*combs_next
                    elif not enough_space or not extension_possible or not before_healthy:
                        if verbose:
                            print("    "*level,"breaking rest of start indices")
                        break
                else:
                    if verbose:
                        print("    "*level,"breaking rest of start indices")
                    break
            return combinations

        spring_group_ext = "?".join(list(repeat(spring_group, 5)))
        damage_sizes_ext = damage_sizes*5
        combs = calc_combinations(spring_group_ext, damage_sizes_ext, 0, cache)
        frame = pd.concat([frame, pd.DataFrame({"no": [idx], "combs": [combs]})], axis=0)
        frame.to_csv("12_2.csv")
        num_arrangements.append(combs)

    print(cache)
    return num_arrangements
 


sol = solution(data, verbose=False)
# sol = solution([data[0]], verbose=True)
# sol = solution(test_data_2, verbose=True)
print(sol)
display(sum(sol))



1/1000
2/1000
3/1000
4/1000
5/1000
6/1000
7/1000
8/1000
9/1000
10/1000
11/1000
12/1000
13/1000
14/1000
15/1000
16/1000
17/1000
18/1000
19/1000
20/1000
21/1000
22/1000
23/1000
24/1000
25/1000
26/1000
27/1000
28/1000
29/1000
30/1000
31/1000
32/1000
33/1000
34/1000
35/1000
36/1000
37/1000
38/1000
39/1000
40/1000
41/1000
42/1000
43/1000
44/1000
45/1000
46/1000
47/1000
48/1000
49/1000
50/1000
51/1000
52/1000
53/1000
54/1000
55/1000
56/1000
57/1000
58/1000
59/1000
60/1000
61/1000
62/1000
63/1000
64/1000
65/1000
66/1000
67/1000
68/1000
69/1000
70/1000
71/1000
72/1000
73/1000
74/1000
75/1000
76/1000
77/1000
78/1000
79/1000
80/1000
81/1000
82/1000
83/1000
84/1000
85/1000
86/1000
87/1000
88/1000
89/1000
90/1000
91/1000
92/1000
93/1000
94/1000
95/1000
96/1000
97/1000
98/1000
99/1000
100/1000
101/1000
102/1000
103/1000
104/1000
105/1000
106/1000
107/1000
108/1000
109/1000
110/1000
111/1000
112/1000
113/1000
114/1000
115/1000
116/1000
117/1000
118/1000
119/1000
120/1000
121/1000
122/1000
123/1000
1

18716325559999